## Implementing the BPE algorithm
The aim of this exercise is to implement the BPE tokenization algorithm. As a reminder, the principle consists in gathering the words or “tokens” that appear the most times in succession.

For example, if we consider the corpus containing the words in the following table (with the number of occurrences of each word):

| words | occurrence |
|------|-----------|
| voting | 2 |
| vote | 3 |
| slow | 1 |
| slowly | 2 |


And if the initial “tokens” are the letters of the alphabet, then the prefix “vo” will initially be added to the list of sub-words (tokens), cause the bigram "v" "o" occurs 5 times (2 + 3).

The steps involved in implementing the BPE algorithm are as follows:
1. Download a text corpus (here a wikipedia page)
2. Cut the text into words (using the “space” and “ponctuation” characters) and count the number of occurrences of each word.
3. Initialize the word dictionary with the initial tokens (letters of the alphabet)
4. Run BPE algorithm (learn vocabulary)
5. Test token decomposition on selected sentences (apply learned rules)


In the documents you will observe a lot of TODO in the code, replace it by your code.


### The class we will complete


At the end we will create an object (python) class as it follows :

```python
class Tokenizer:
    ''' 
        A class for our Tokenizer

        Methods
        -------
        fit(text_corpus: str) : None
            Fit the tokenizer based on the input text corpus 
        tokenize(text: str): List[str]
            Tokenize a text and return the list of token ids
        detokenize(tokens: List[str]): str
            From a list of token ids return the corresponding text
    '''

    def __init__(self, vocabulary_size: int = 500):
        ''' 
            Parameters
            ----------
            vocabulary_size : int
                The expected size of the vocabulary

        '''
        super().__init__()
        self.vs = vocabulary_size

    def fit(self, text_corpus: str):
        ''' Train the tokenizer on the provided text.

            Parameters
            ----------
            text_corpus : str
                The text used to train the model
        '''
        raise NotImplementedError


    def tokenize(self, text: str) -> List[str]:
        ''' Tokenize a text.

            Parameters
            ----------
            text : str
                The text to tokenize

            Returns
            -------
            List[str]
                The list of tokens
        '''
        raise NotImplementedError

    def detokenize(self, tokens : List[int]) -> str:
        ''' Reverse the tokenization.

            Parameters
            ----------
            tokens : List[str]
                A list of token ids

            Returns
            -------
            str
                The text corresponding to tokens
        '''
        raise NotImplementedError

```

## Requirement

**For this lab you only need the python standard library :D**

In [77]:
import re # the regex library
import json # read export json format

from typing import List, Dict, Tuple # to specify the types in function def
from collections import Counter # a tools to counts unique occurences
from IPython.core.display import display, HTML # just for pretty print

from urllib.request import urlopen, Request

/tmp/ipykernel_134797/2305373172.py:6: DeprecationWarning: Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython.display
  from IPython.core.display import display, HTML # just for pretty print


### Step 1: Download a corpus

For this lab we will consider a wikipedia page in french [Grèce antique](https://fr.wikipedia.org/w/api.php?format=json&action=query&prop=extracts&explaintext&redirects=1&titles=Gr%C3%A8ce_antique), but you are free to choose any content you want !

In [ ]:
url_request  = 'https://fr.wikipedia.org/w/api.php?format=json&action=query&prop=extracts&explaintext&redirects=1&titles=Gr%C3%A8ce_antique'
wikipedia_request = Request(url_request)
wikipedia_request.add_header("User-Agent", "Course (thomas.gerald@lisn.fr)")
raw_page = urlopen(wikipedia_request)
json_page = json.load(raw_page)


In [ ]:
corpus = list(json_page['query']['pages'].values())[0]['extract']

### Step 2: Splitting text into words (or sequence of character no containing space)

To split the text into words, we'll use the following regex ```r'(\b[^\s]+\b)'```. To count words, we'll use python's Counter object. 
1. Store each word and its number of occurrences in **count_words** using the [Counter Object](https://docs.python.org/3/library/collections.html#collections.Counter).
2. Print the 10 most frequent words using the method **most_commons** of the Counter object.


In [ ]:

word_regex = re.compile(r'(\b[^\s]+\b)')
words = word_regex.findall(corpus)

count_words =  # TODO
most_commons_words =  # TODO
display(HTML(f"""
<p>The most common words are : </p>
<table> 
\t<tr><th> Word </th> <th> Rank </th> <th> Number of occurrences <tr>
\t{'\n\t'.join([f'<tr><th>{k}</th><th>{i+1}</th><th>{v}</th></tr>'
           for i, (k, v) in enumerate(most_commons_words)])}
<table>"""
))

### Step 3: Initialize word dictionary with initial tokens (letters of the alphabet)

Create the initial vocabulary in the vocab variable, we recall that we consider characters as base tokens. How many initial tokens do you have?

In [ ]:
vocab =  # TODO
vocab.sort()
vocab
print(f"we have {len(vocab)} initial tokens")

we have 107 initial tokens


### Step 4: Learning the tokenizer
To learn the tokenizer we need several functions:
1. A function to calculate the frequency of each token pair.
2. A function to merge a pair

Several variables will be required:
1. **vocab** containing current vocabulary
2. **merge_rules** containing all the merge rules (a dictionary containing as key a pair of tokens to merge and the result of the token merge). For example: {('e', 's'), 'es', ('en', 't') :'ent'}.
3. **splits** A dictionary containing the current breakdown of the corpus, with the word as key and the list of “tokens” as value.

#### Step 4.1: Splitting words into tokens
In the first step splits contains the words broken down into characters. For instance if we consider the words "La", "Grèce", "Antique", "est" we should have into the splits variables the following structure :

```python
{
    'La': ['L', 'a'],
    'Grèce': ['G', 'r', 'è', 'c', 'e'],
    'antique': ['a', 'n', 't', 'i', 'q', 'u', 'e'],
    'est': ['e', 's', 't'],
    'une': ['u', 'n', 'e']
}
```


In [ ]:
# In the first step splits contains the words broken down into characters
splits = # TODO
print("\n".join([f"{k} -> {'-'.join([v for v in splits[k]])}" for k in list(splits.keys())[:10]]))

La -> L-a
Grèce -> G-r-è-c-e
antique -> a-n-t-i-q-u-e
est -> e-s-t
une -> u-n-e
civilisation -> c-i-v-i-l-i-s-a-t-i-o-n
de -> d-e
l'Antiquité -> l-'-A-n-t-i-q-u-i-t-é
des -> d-e-s
peuples -> p-e-u-p-l-e-s


#### Step 4.2: Compute the frequency of token pairs
Create a function **compute_pair_freqs**, which, given the words broken down into tokens (splits dictionary) and the frequency of the words, returns the frequency of each pair of tokens (note only successive sub-words).

In [ ]:
def compute_pair_freqs(splits, word_freqs):
    raise NotImplementedError

In [114]:
pair_freqs = compute_pair_freqs(splits, count_words)
print("\n".join([f" The pair of tokens {k} occur {pair_freqs[k]} times in the corpus" for k  in list(pair_freqs.keys())[:5]]))

 The pair of tokens ('L', 'a') occur 166 times in the corpus
 The pair of tokens ('G', 'r') occur 257 times in the corpus
 The pair of tokens ('r', 'è') occur 249 times in the corpus
 The pair of tokens ('è', 'c') occur 285 times in the corpus
 The pair of tokens ('c', 'e') occur 1191 times in the corpus


#### Step 4.3: Find the most frequent pair
Create a function **most_frequent(pair_freqs)** returning the most frequent pair of tokens. You can use the function `max` provided by python.


In [ ]:
def most_frequent(pair_freqs):
    raise NotImplementedError
print(f"The most frequent pair is {most_frequent(pair_freqs)}")

The most frequent pair is ('e', 's')


#### Step 4.4: Merge all tokens from the retrieved pair
Create a **merge_pair()** function which, given a pair, returns the new splits of the corpus.

In [ ]:
def merge_pair(a : str, b: str, splits : Dict[str, List[str]]) -> Dict[str, List[str]]:
    ''' Merge tokens where a.b

        Parameters
        ----------
        a : str
            The first token of the pair
        b : str
            The first token of the pair
        splits : Dict[str, List[str]
            The dataset considering tokenized words

        Returns
        -------
         Dict[str, List[str]
            The new split with tokens a and b merged
    '''
    raise NotImplementedError

In [117]:
new_splits = merge_pair(*most_frequent(pair_freqs), splits)
print(new_splits['grecques'])

['g', 'r', 'e', 'c', 'q', 'u', 'es']


#### Apply the algorithm until the desired vocabulary size is reached.
Create a BPE object that takes as arguments a corpus, a vocabulary size and train the BPE algorithm. The algorithm stores the final vocabulary in the **vocabulary** attribute and the merge rules in **mr**. The attributes **mr** will be a list of couple of tokens 
```
[('e', 's'),
 ('n', 't'),
 ('q', 'u'),
 ('r', 'e'),
 ('o', 'n'),
 ('d', 'e'),
 ('l', 'e'),
 ('t', 'i'),
 ('l', 'a'),
 ('i', 's'),
 ('e', 'nt'), ...
]
```

In [ ]:
class BPETokenizer:
    ''' 
        A class for our Tokenizer

        Methods
        -------
        fit(text_corpus: str) : None
            Fit the tokenizer based on the input text corpus 
        tokenize(text: str): List[str]
            Tokenize a text and return the list of token ids
        detokenize(tokens: List[str]): str
            From a list of token ids return the corresponding text
    '''
    @staticmethod    
    def compute_pair_freqs(splits: Dict[str, List[str]], word_freqs: Dict[str, int]) -> Dict[Tuple[str, str], int]:
        return compute_pair_freqs(splits, word_freqs)
    
    @staticmethod
    def most_frequent(pair_freqs: Dict[Tuple[str, str], int]) -> Tuple[str, str]:
        return most_frequent(pair_freqs)
    
    @staticmethod 
    def merge_pair(a : str, b: str, splits : Dict[str, List[str]]) -> Dict[str, List[str]]:
        return merge_pair(a, b, splits)
    


    def __init__(self, vocabulary_size: int = 500):
        ''' 
            Parameters
            ----------
            vocabulary_size : int
                The expected size of the vocabulary

        '''
        super().__init__()
        self.vs = vocabulary_size
        self.vocab = []
        self.wr = re.compile(r'(\b[^\s]+\b)') # the regex to split onto space
        self.mr = [] # the merge rules in the same order as the one retrieved


    def fit(self, text_corpus: str):
        ''' Train the tokenizer on the provided text.

            Parameters
            ----------
            text_corpus : str
                The text used to train the model
        '''
        words = self.wr.findall(text_corpus)

        # initialize the vocabulary (using characters)
        self.vocab = # TODO
        # get the number of occurences of each words
        word_freqs = # TODO
        # tokenize each word of the dataset (according to vocab which is here the characters)
        splits = # TODO 

        # while we did not reach the desired vocabulary size
        while len(self.vocab) < self.vs:
            raise NotImplementedError

    def tokenize(self, text: str) -> List[List[str]]:
        ''' Tokenize a text.

            Parameters
            ----------
            text : str
                The text to tokenize

            Returns
            -------
            List[str]
                The list of tokens
        '''
        words = self.wr.findall(text)
        splits = [[l for l in word] for word in words]
        for prefix, suffix in self.mr:
            raise NotImplementedError
        return splits

    def detokenize(self, tokens : List[List[str]]) -> str:
        ''' Reverse the tokenization.

            Parameters
            ----------
            tokens : List[str]
                A list of token ids

            Returns
            -------
            str
                The text corresponding to tokens
        '''
        return ' '.join([ "".join(w) for w in tokens])


In [218]:
my_bpe = BPETokenizer(vocabulary_size=5000)
my_bpe.fit(corpus)


In [222]:
texte = '''Anti blpqsdinjz ajfrfjqk grecques développée en Grèce '''
print(my_bpe.tokenize(texte))
my_bpe.detokenize(my_bpe.tokenize(texte))

[['Anti'], ['b', 'l', 'p', 'q', 's', 'd', 'in', 'j', 'z'], ['a', 'j', 'f', 'r', 'f', 'j', 'q', 'k'], ['grecques'], ['développée'], ['en'], ['Grèce']]


'Anti blpqsdinjz ajfrfjqk grecques développée en Grèce'

#### Test by modifying parameters or corpus
Test the algorithm with different hyper-parameters or data

## Using sentencepiece
We're now going to use the `sentencepiece` library, which can be installed (if not already installed) with pip : 

`! pip install sentencepiece`

To train the tokenizer, we'll use the `train` function of `SentencePieceTrainer`. 

In [195]:
import sentencepiece as spm

with open("test-cours.txt", "w") as f:
    f.write(corpus)
spm.SentencePieceTrainer.train(input="test-cours.txt", model_type='BPE',  model_prefix='m', vocab_size=500)

sentencepiece_trainer.cc(78) LOG(INFO) Starts training with : 
trainer_spec {
  input: test-cours.txt
  input_format: 
  model_prefix: m
  model_type: BPE
  vocab_size: 500
  self_test_sample_size: 0
  character_coverage: 0.9995
  input_sentence_size: 0
  shuffle_input_sentence: 1
  seed_sentencepiece_size: 1000000
  shrinking_factor: 0.75
  max_sentence_length: 4192
  num_threads: 16
  num_sub_iterations: 2
  max_sentencepiece_length: 16
  split_by_unicode_script: 1
  split_by_number: 1
  split_by_whitespace: 1
  split_digits: 0
  pretokenization_delimiter: 
  treat_whitespace_as_suffix: 0
  allow_whitespace_only_pieces: 0
  required_chars: 
  byte_fallback: 0
  vocabulary_output_piece_score: 1
  train_extremely_large_corpus: 0
  seed_sentencepieces_file: 
  hard_vocab_limit: 1
  use_all_vocab: 0
  unk_id: 0
  bos_id: 1
  eos_id: 2
  pad_id: -1
  unk_piece: <unk>
  bos_piece: <s>
  eos_piece: </s>
  pad_piece: <pad>
  unk_surface:  ⁇ 
  enable_differential_privacy: 0
  differential_pr

Looking at the “m.vocab” file, what are the differences with the vocabulary learned with your implementation? What modifications could you consider to obtain a similar vocabulary?

## Detokenization and space characters

Propose and implement a methods to detokenize encoded sentence (you should want to extend your vocabulary).


**Hint :** One modification (or addition) in the function `fit` and One (or two) modification in the tokenize function
